In [1]:
import sys
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse

In [4]:
ensembl_df = pd.DataFrame(pd.read_csv("/booleanfs2/sahoo/Data/SeqData/genome/Mus_musculus.GRCm38.94.txt", sep = '\t', header=None)) 
ensembl_df.columns = ["ProbeID", "Name"]
ensembl_df.merge(expr, how="right\",on="ProbeID")
ensembl_df

ProbeID            Name
0      ENSMUSG00000102693   4933401J01Rik
1      ENSMUSG00000064842         Gm26206
2      ENSMUSG00000051951            Xkr4
3      ENSMUSG00000102851         Gm18956
4      ENSMUSG00000103377         Gm37180
...                   ...             ...
54527  ENSMUSG00000094431  CAAA01205117.1
54528  ENSMUSG00000094621  CAAA01098150.1
54529  ENSMUSG00000098647  CAAA01064564.1
54530  ENSMUSG00000096730        Vmn2r122
54531  ENSMUSG00000095742  CAAA01147332.1

[54532 rows x 2 columns]

In [10]:
expr = pd.DataFrame(pd.read_csv("GSE141745_normalized_tpm.csv", sep=",", header=0))
ih_df = pd.read_csv("GSE141745-GPL17021-ih.txt", sep="\t", header=0) 
expr.columns = ["ProbeID"]+list(ih_df["ArrayID"])
ensembl_df = pd.DataFrame(pd.read_csv("/booleanfs2/sahoo/Data/SeqData/genome/Mus_musculus.GRCm38.94.txt", sep = '\t', header=None)) 
ensembl_df.columns = ["ProbeID", "Name"]
expr = ensembl_df.merge(expr, how="right",on="ProbeID")
expr

ProbeID          Name  GSM4212680  GSM4212681  GSM4212682  \
0      ENSMUSG00000000001         Gnai3  237.167713  407.174345  687.080938   
1      ENSMUSG00000000003          Pbsn    0.130671    0.039674    0.056139   
2      ENSMUSG00000000028         Cdc45    0.914696    1.944026    2.413962   
3      ENSMUSG00000000037         Scml2    0.130671    0.039674    0.056139   
4      ENSMUSG00000000049          Apoh    0.130671    0.039674    0.056139   
...                   ...           ...         ...         ...         ...   
32323  ENSMUSG00000109571       Gm44655    0.130671    0.039674    0.056139   
32324  ENSMUSG00000109572        Cfap99    0.130671    0.039674    0.056139   
32325  ENSMUSG00000109573  Olfr1473-ps1    0.130671    0.039674    0.056139   
32326  ENSMUSG00000109577       Gm44543    0.130671    0.039674    0.056139   
32327  ENSMUSG00000109578       Gm16475    0.130671    0.039674    0.056139   

       GSM4212683  GSM4212684  GSM4212685  GSM4212686  GSM4212687  GSM4212688  \
0      381.666957  423.964485  496.580039  246.546351  334.755561  670.475750   
1        0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   
2       11.244820   11.743464    4.493295    0.073574    0.216390    4.185236   
3        0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   
4        0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   
...           ...         ...         ...         ...         ...         ...   
32323    0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   
32324    0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   
32325    0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   
32326    0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   
32327    0.038642    0.036357    0.047298    0.073574    0.216390    0.093005   

       GSM4212689  GSM4212690  GSM4212691  GSM4212692  GSM4212693  GSM4212694  \
0      789.457665  490.570635  661.911126  651.502985  890.898835  714.854152   
1        0.059812    0.054429    0.052082    0.052175    0.057142    0.048317   
2        2.452289    5.170777   12.239309    8.295749   25.656698   11.354561   
3        0.059812    0.054429    0.156246    0.052175    0.057142    0.048317   
4        0.059812    0.054429    0.052082    0.052175    0.057142    0.048317   
...           ...         ...         ...         ...         ...         ...   
32323    0.059812    0.054429    0.052082    0.052175    0.057142    0.048317   
32324    0.059812    0.054429    0.052082    0.052175    0.057142    0.048317   
32325    0.059812    0.054429    0.052082    0.052175    0.057142    0.048317   
32326    0.059812    0.054429    0.052082    0.052175    0.057142    0.048317   
32327    0.059812    0.054429    0.052082    0.052175    0.057142    0.048317   

       GSM4212695  GSM4212696  GSM4212697  
0      143.887003  186.776634  213.101425  
1        0.053193    0.041497    0.038390  
2        8.564069    3.029259    2.725671  
3        0.053193    0.041497    7.639560  
4        0.053193    0.041497    0.038390  
...           ...         ...         ...  
32323    0.053193    0.041497    0.038390  
32324    0.053193    0.041497    0.038390  
32325    0.053193    0.041497    0.038390  
32326    0.053193    0.041497    0.038390  
32327    0.053193    0.041497    0.038390  

[32328 rows x 20 columns]

In [11]:
genes = pd.DataFrame()
genes["ProbeID"] = expr["ProbeID"]
genes["Name"] = expr["Name"]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
#sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

path_dir = "./"
expr.to_csv(path_dir+"GSE141745-GPL17021-expr.txt", header=True, index=False,sep='\t')
expr

/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID          Name  GSM4212680  GSM4212681  GSM4212682  \
0      ENSMUSG00000000001         Gnai3    7.895834    8.673041    9.426435   
1      ENSMUSG00000000003          Pbsn    0.177179    0.056131    0.078799   
2      ENSMUSG00000000028         Cdc45    0.937116    1.557791    1.771447   
3      ENSMUSG00000000037         Scml2    0.177179    0.056131    0.078799   
4      ENSMUSG00000000049          Apoh    0.177179    0.056131    0.078799   
...                   ...           ...         ...         ...         ...   
32323  ENSMUSG00000109571       Gm44655    0.177179    0.056131    0.078799   
32324  ENSMUSG00000109572        Cfap99    0.177179    0.056131    0.078799   
32325  ENSMUSG00000109573  Olfr1473-ps1    0.177179    0.056131    0.078799   
32326  ENSMUSG00000109577       Gm44543    0.177179    0.056131    0.078799   
32327  ENSMUSG00000109578       Gm16475    0.177179    0.056131    0.078799   

       GSM4212683  GSM4212684  GSM4212685  GSM4212686  GSM4212687  GSM4212688  \
0        8.579946    8.731198    8.958785    7.951555    8.391268    9.391191   
1        0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   
2        3.614100    3.671685    2.457672    0.102422    0.282606    2.374410   
3        0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   
4        0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   
...           ...         ...         ...         ...         ...         ...   
32323    0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   
32324    0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   
32325    0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   
32326    0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   
32327    0.054698    0.051522    0.066672    0.102422    0.282606    0.128301   

       GSM4212689  GSM4212690  GSM4212691  GSM4212692  GSM4212693  GSM4212694  \
0        9.626545    8.941255    9.372672    9.349841    9.800736    9.483521   
1        0.083808    0.076462    0.073247    0.073374    0.080169    0.068075   
2        1.787553    2.625452    3.726756    3.216571    4.736426    3.626972   
3        0.083808    0.076462    0.209449    0.073374    0.080169    0.068075   
4        0.083808    0.076462    0.073247    0.073374    0.080169    0.068075   
...           ...         ...         ...         ...         ...         ...   
32323    0.083808    0.076462    0.073247    0.073374    0.080169    0.068075   
32324    0.083808    0.076462    0.073247    0.073374    0.080169    0.068075   
32325    0.083808    0.076462    0.073247    0.073374    0.080169    0.068075   
32326    0.083808    0.076462    0.073247    0.073374    0.080169    0.068075   
32327    0.083808    0.076462    0.073247    0.073374    0.080169    0.068075   

       GSM4212695  GSM4212696  GSM4212697  
0        7.178784    7.552874    7.742150  
1        0.074770    0.058658    0.054348  
2        3.257624    2.010514    1.897500  
3        0.074770    0.058658    3.110958  
4        0.074770    0.058658    0.054348  
...           ...         ...         ...  
32323    0.074770    0.058658    0.054348  
32324    0.074770    0.058658    0.054348  
32325    0.074770    0.058658    0.054348  
32326    0.074770    0.058658    0.054348  
32327    0.074770    0.058658    0.054348  

[32328 rows x 20 columns]

In [12]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE141745-GPL17021-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE141745-GPL17021-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
